In [1]:
from shapely.geometry import Point 
from shapely.geometry import LineString
import pandas as pd
import geopandas as gpd
import sys
import matplotlib.pyplot as plt
import datetime
import numpy as np
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster

# Adding csv data

In [2]:
tornado_911 = pd.read_csv('../data/911_Phone_Calls_Tornado_030320.csv')
cadd_tornado = pd.read_csv('../data/Computer_Aided_Dispatch_Data_Tornado_Incidents_030320.csv', skiprows = 3)
derecho_911 = pd.read_csv('../data/911_Phone_Calls_Derecho_050320_050420.csv')
cadd_derecho = pd.read_csv('../data/Computer_Aided_Dispatch_Data_Derecho_Incidents_050320-050420.csv', skiprows = 3)

# Fixing columns

In [3]:
tornado_911.columns = ['time', 'calltype', 'lat', 'lng', 'cell_tower_address']
derecho_911.columns = ['time', 'calltype', 'lat', 'lng', 'cell_tower_address']
cadd_tornado.columns = ['time', 'location', 'lat', 'lng', 'incident_type']
cadd_derecho.columns = ['time', 'location', 'lat', 'lng', 'incident_type']

In [4]:
tornado_911.time = pd.to_datetime(tornado_911.time)
derecho_911.time = pd.to_datetime(derecho_911.time)
cadd_tornado.time = pd.to_datetime(cadd_tornado.time)
cadd_derecho.time = pd.to_datetime(cadd_derecho.time)

In [5]:
tornado_911 = tornado_911.dropna(subset = ['lat', 'lng'])
derecho_911 = derecho_911.dropna(subset = ['lat', 'lng'])
cadd_tornado = cadd_tornado.dropna(subset = ['lat', 'lng'])
cadd_derecho = cadd_derecho.dropna(subset = ['lat', 'lng'])

In [6]:
tornado_911['geometry'] = tornado_911.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
derecho_911['geometry'] = derecho_911.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
cadd_tornado['geometry'] = cadd_tornado.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
cadd_derecho['geometry'] = cadd_derecho.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)

### Check them here

In [7]:
#tornado_911.head()

In [8]:
#derecho_911.head()

In [9]:
#cadd_tornado.head()

In [10]:
#cadd_derecho.head()

# Breaking down the dataframes by time

### For Tornado 911 Calls

In [11]:
torn_check = tornado_911.groupby(by=[pd.Grouper(key = 'time', freq='1h'), "calltype"]).count().reset_index()
torn_check

time   calltype  lat  lng  cell_tower_address  geometry
0 2020-03-03 00:00:00  911 Calls   93   93                  93        93
1 2020-03-03 01:00:00  911 Calls  187  187                 187       187
2 2020-03-03 02:00:00  911 Calls   80   80                  80        80
3 2020-03-03 03:00:00  911 Calls   45   45                  45        45
4 2020-03-03 04:00:00  911 Calls   45   45                  45        45

In [12]:
midnight_torn_calls = tornado_911[tornado_911.time < '2020-03-03 01:00:00']
one_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 00:59:59') & (tornado_911.time < '2020-03-03 02:00:00')]
two_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 01:59:59') & (tornado_911.time < '2020-03-03 03:00:00')]
three_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 02:59:59') & (tornado_911.time < '2020-03-03 04:00:00')]
four_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 03:59:59') & (tornado_911.time < '2020-03-03 05:00:00')]

### For CADD Tornado Responses

In [13]:
cadd_tornado_count = cadd_tornado
cadd_tornado_count['count'] = 1
cadd_torn_check = cadd_tornado_count.groupby(by=[pd.Grouper(key = 'time', freq='1h'), 'count']).count().reset_index()
cadd_torn_check

time  count  location  lat  lng  incident_type  geometry
0 2020-03-03 00:00:00      1        44   44   44             44        44
1 2020-03-03 01:00:00      1        85   85   85             85        85
2 2020-03-03 02:00:00      1        69   69   69             69        69
3 2020-03-03 03:00:00      1        31   31   31             31        31
4 2020-03-03 04:00:00      1        31   31   31             31        31

In [14]:
midnight_cadd_torn_calls = cadd_tornado[cadd_tornado.time < '2020-03-03 01:00:00']
one_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 00:59:59') & (cadd_tornado.time < '2020-03-03 02:00:00')]
two_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 01:59:59') & (cadd_tornado.time < '2020-03-03 03:00:00')]
three_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 02:59:59') & (cadd_tornado.time < '2020-03-03 04:00:00')]
four_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 03:59:59') & (cadd_tornado.time < '2020-03-03 05:00:00')]

### For Derecho 911 Calls

In [35]:
derecho_911_check = derecho_911
derecho_911_check['count'] = 1
derecho_911_check = derecho_911_check.groupby(by=[pd.Grouper(key = 'time', freq='30min'), 'calltype']).count().reset_index()
derecho_911_check

time   calltype  lat  lng  cell_tower_address  geometry  \
0  2020-05-03 16:30:00  911 Calls  138  138                 138       138   
1  2020-05-03 17:00:00  911 Calls  110  110                 110       110   
2  2020-05-03 17:30:00  911 Calls  146  146                 146       146   
3  2020-05-03 18:00:00  911 Calls  148  148                 148       148   
4  2020-05-03 18:30:00  911 Calls  188  188                 188       188   
5  2020-05-03 19:00:00  911 Calls  151  151                 151       151   
6  2020-05-03 19:30:00  911 Calls  108  108                 108       108   
7  2020-05-03 20:00:00  911 Calls  111  111                 111       111   
8  2020-05-03 20:30:00  911 Calls   76   76                  76        76   
9  2020-05-03 21:00:00  911 Calls   63   63                  63        63   
10 2020-05-03 21:30:00  911 Calls   56   56                  56        56   
11 2020-05-03 22:00:00  911 Calls   75   75                  75        75   
12 2020-05-03 22:30:00  911 Calls   50   50                  50        50   
13 2020-05-03 23:00:00  911 Calls   24   24                  24        24   
14 2020-05-03 23:30:00  911 Calls   23   23                  23        23   
15 2020-05-04 00:00:00  911 Calls   16   16                  16        16   

    count  
0     138  
1     110  
2     146  
3     148  
4     188  
5     151  
6     108  
7     111  
8      76  
9      63  
10     56  
11     75  
12     50  
13     24  
14     23  
15     16

# Adding geojson data

In [15]:
damage_points = gpd.read_file('../data/damage_points.geojson')
path_polygons = gpd.read_file('../data/path_polygons.geojson')
tornado_paths = gpd.read_file('../data/tornado_paths.geojson')

# Fixing columns

In [16]:
damage_points.stormdate = damage_points.stormdate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
damage_points.surveydate = damage_points.surveydate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.stormdate = tornado_paths.stormdate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.starttime = tornado_paths.starttime.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.endtime = tornado_paths.endtime.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))

### Check them here

In [17]:
#damage_points.head()

In [18]:
#path_polygons.head()

In [19]:
#tornado_paths

# Making GeoDataFrames

In [20]:
geo_tornado_911 = gpd.GeoDataFrame(tornado_911, crs = tornado_paths.crs, geometry = tornado_911.geometry)
geo_derecho_911 = gpd.GeoDataFrame(derecho_911, crs = tornado_paths.crs, geometry = derecho_911.geometry)
geo_cadd_tornado = gpd.GeoDataFrame(cadd_tornado, crs = tornado_paths.crs, geometry = cadd_tornado.geometry)
geo_cadd_derecho = gpd.GeoDataFrame(cadd_derecho, crs = tornado_paths.crs, geometry = cadd_derecho.geometry)

# Filtering for the Nashville Tornado

In [21]:
nashville_tornado = tornado_paths.loc[tornado_paths.event_id == 'Nashville']
nashville_path = path_polygons.geometry.iloc[np.r_[4, 10:25, 26:35]]
nashville_path = nashville_path.reset_index()
nashville_path = nashville_path.drop(columns = ['index'])
nashville_damage = gpd.sjoin(damage_points, nashville_path, how = 'inner', op = 'within')
nashville_damage = nashville_damage.drop_duplicates(keep = 'first', subset = ['geometry'])

### Check them here

In [22]:
#nashville_tornado

In [23]:
#nashville_path

In [24]:
#nashville_damage.head()

# Mapping the Nashville Tornado

### Calls

In [25]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_calls = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_calls)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_calls)

for row_index, row_values in midnight_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'red', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in one_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'orange', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in two_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'green', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in three_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'darkblue', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in four_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'purple', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
map_calls

### CADD Response

In [26]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_cadd_res = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_cadd_res)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_cadd_res)

for row_index, row_values in midnight_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'red')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in one_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'orange')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in two_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'green')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in three_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'darkblue')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in four_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'purple')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
map_cadd_res

### Damage

In [28]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_damage = folium.Map(location = startloc, zoom_start = 10)

marker_cluster = MarkerCluster().add_to(map_damage)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_damage)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_damage)

    
for row_index, row_values in nashville_damage.iterrows():
    loc = [row_values['lat'], row_values['lon']]
    pop = 'Happened on: ' + str(row_values['stormdate']) + '. Surveyed on: ' + str(row_values['surveydate']) + '. Damage Caused: ' + str(row_values['damage_txt']) + ' ' + str(row_values['dod_txt']) + '. This caused ' + str(row_values['injuries']) + ' injuries and ' + str(row_values['deaths']) + ' deaths.'
    icon = folium.Icon(color = 'orange')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(marker_cluster)


map_damage

In [32]:
nashville_damage.head()

objectid           stormdate          surveydate      event_id  damage  \
0   2047717 2020-03-03 00:57:00 2020-03-04 09:28:00  Mount Juliet       2   
3   2060941 2020-03-03 00:43:00 2020-03-26 12:09:00                     1   
4   2060984 2020-03-03 00:43:00 2020-03-26 16:00:00                     7   
5   2090491 2020-03-03 00:44:00 2020-04-19 03:18:00                     1   
6   2098070 2020-03-03 00:52:00 2020-04-23 00:24:00                     1   

                                  damage_txt  \
0       One- or Two-Family Residences (FR12)   
3     Small Barns or Farm Outbuildings (SBO)   
4  Masonry Apartment or Motel Building (MAM)   
5     Small Barns or Farm Outbuildings (SBO)   
6     Small Barns or Farm Outbuildings (SBO)   

                             dod_txt efscale damage_dir windspeed  ...  qc  \
0                All walls collapsed     EF3        N/A       155  ...   Y   
3      Total destruction of building     EF1        N/A        95  ...   Y   
4       Loss of roof covering (<20%)     EF0        N/A        80  ...   Y   
5      Total destruction of building     EF1        N/A       105  ...   Y   
6  Loss of wood or metal roof panels     EF0        N/A        85  ...   Y   

   dod  surveytype                                globalid edit_user  \
0    9        None  {FE82BBAC-ABF8-4562-81F6-A527829FBFFE}      None   
3    8        None  {A0744CB4-5993-4056-A13C-CF75182F5147}      None   
4    2        None  {DA83D428-084A-4ACA-A39E-DEE84AA28463}      None   
5    8        None  {F885805B-9BD4-448C-9855-CC2D5425AC43}      None   
6    2        None  {18B795BC-211B-4B14-A8F5-2A68167D6B25}      None   

  edit_time comments path_guid                    geometry  index_right  
0      None     none      None  POINT (-86.51628 36.18344)            0  
3      None     None      None  POINT (-86.76228 36.17340)            0  
4      None     None      None  POINT (-86.75692 36.17568)            0  
5      None     None      None  POINT (-86.73612 36.17429)            0  
6      None     None      None  POINT (-86.62517 36.18382)            0  

[5 rows x 28 columns]